<a href="https://colab.research.google.com/github/otmive/diffusion_classifier_clip/blob/main/clip_finetune.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# To train all models:

In [ ]:
!pip install git+https://github.com/openai/CLIP.git

  Cloning https://github.com/openai/CLIP.git to /tmp/pip-req-build-9zt2t6xr
  Running command git clone --filter=blob:none --quiet https://github.com/openai/CLIP.git /tmp/pip-req-build-9zt2t6xr
  Resolved https://github.com/openai/CLIP.git to commit dcba3cb2e2827b402d2701e7e1c7d9fed8a20ef1
  Preparing metadata (setup.py) ... done
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using c

In [ ]:
from PIL import Image
import torch
from torch import nn, optim
import glob
import os
import pandas as pd
import json
import numpy as np
import clip
from torch.utils.data import Dataset, DataLoader, BatchSampler
from sklearn.model_selection import train_test_split
from tqdm.notebook import tqdm
import random
from matplotlib.pyplot import imshow
import torchtext
import nltk, re, string, collections
from nltk.util import ngrams
import collections
%matplotlib inline
BATCH_SIZE = 8
EPOCH = 20

In [ ]:
from google.colab import drive
drive.mount('/content/drive')


Mounted at /content/drive


In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"
model, preprocess = clip.load("ViT-B/32", device=device, jit=False)

100%|███████████████████████████████████████| 338M/338M [00:04<00:00, 87.4MiB/s]


# Single Object

In [ ]:
# get single object data from drive
!cp /content/drive/MyDrive/single_object\ \(4\).zip /content/single_object.zip
!unzip single_object.zip

Archive:  single_object.zip
   creating: single_object/
   creating: single_object/val/
   creating: single_object/val/gray cylinder/
  inflating: single_object/val/gray cylinder/CLEVR_new_small_gray_rubber_cylinder000068.png  
  inflating: single_object/val/gray cylinder/CLEVR_new_small_gray_rubber_cylinder000082.png  
  inflating: single_object/val/gray cylinder/CLEVR_new_small_gray_rubber_cylinder000035.png  
  inflating: single_object/val/gray cylinder/CLEVR_new_large_gray_rubber_cylinder000096.png  
  inflating: single_object/val/gray cylinder/CLEVR_new_small_gray_metal_cylinder000073.png  
  inflating: single_object/val/gray cylinder/CLEVR_new_small_gray_metal_cylinder000075.png  
  inflating: single_object/val/gray cylinder/CLEVR_new_large_gray_metal_cylinder000017.png  
  inflating: single_object/val/gray cylinder/CLEVR_new_large_gray_metal_cylinder000036.png  
  inflating: single_object/val/gray cylinder/CLEVR_new_small_gray_rubber_cylinder000014.png  
  inflating: single_obje

In [ ]:
# prompt: randomly sample 30 images from each subfolder in single_object/train and put in a new folder with the same subfolders as single_object/train

import shutil
import os

def sample_images(source_dir, dest_dir, num_samples):
  if not os.path.exists(dest_dir):
    os.makedirs(dest_dir)

  # make subfolders in destination folder
  for subfolder in os.listdir(source_dir):
    if not os.path.exists(os.path.join(dest_dir, subfolder)):
      os.makedirs(os.path.join(dest_dir, subfolder))

    subfolder_path = os.path.join(source_dir, subfolder)

    # take random images so there's still a mix of sizes/materials in the new folder
    images = [f for f in os.listdir(subfolder_path)]
    random_images = random.sample(images, min(num_samples, len(images)))
    for image in random_images:
      shutil.copy(os.path.join(subfolder_path, image), os.path.join(dest_dir, subfolder, image))



# Example usage:
source_dir = 'single_object/train'
dest_dir = 'train30'
sample_images(source_dir, dest_dir, 30)


In [ ]:
!cp /content/drive/MyDrive/train30.zip /content/
!unzip train30.zip

Archive:  train30.zip
   creating: train30/
   creating: train30/yellow sphere/
  inflating: train30/yellow sphere/CLEVR_new_large_yellow_metal_sphere000088.png  
  inflating: train30/yellow sphere/CLEVR_new_small_yellow_metal_sphere000095.png  
  inflating: train30/yellow sphere/CLEVR_new_large_yellow_metal_sphere000024.png  
  inflating: train30/yellow sphere/CLEVR_new_large_yellow_rubber_sphere000059.png  
  inflating: train30/yellow sphere/CLEVR_new_large_yellow_rubber_sphere000076.png  
  inflating: train30/yellow sphere/CLEVR_new_large_yellow_rubber_sphere000033.png  
  inflating: train30/yellow sphere/CLEVR_new_small_yellow_metal_sphere000001.png  
  inflating: train30/yellow sphere/CLEVR_new_small_yellow_metal_sphere000039.png  
  inflating: train30/yellow sphere/CLEVR_new_small_yellow_rubber_sphere000011.png  
  inflating: train30/yellow sphere/CLEVR_new_large_yellow_metal_sphere000015.png  
  inflating: train30/yellow sphere/CLEVR_new_large_yellow_rubber_sphere000012.png  
  

In [ ]:
d_train = {}
for folder in os.listdir('/content/train30/'):
  for img_path in glob.glob('/content/train30/' + folder + "/*.png"):
    d_train[img_path] = ["a photo of a " + folder]

len(d_train)

510

In [ ]:
class ClevrDataset(Dataset):
    def __init__(self, data, preprocess):
        self.preprocess = preprocess
        self.img_paths = []
        self.captions = []
        classes = pd.read_csv('clevr_prompts_cone.csv')
        self.class_to_idx = classes['prompt'].tolist()
        for img_path, captions in data.items():
            for cap in captions:
                self.img_paths.append(img_path)
                self.captions.append(cap)
        self.processed_cache = {}
        for img_path in data:
            self.processed_cache[img_path] = self.preprocess(Image.open(img_path))
        self.img_paths_set = list(data.keys())
        self.path2label = {path: self.class_to_idx.index("a photo of a " + path.split('/')[3]) for path in self.img_paths_set}

    def __len__(self):
        return len(self.captions)

    def __getitem__(self, idx):
        img_path = self.img_paths[idx]
        image = self.processed_cache[img_path]
        caption = self.captions[idx]
        label = self.path2label[img_path]
        return image, caption, label

train_dataset = ClevrDataset(d_train, preprocess)

len(train_dataset), train_dataset[0]

(510,
 (tensor([[[-0.2448, -0.2302, -0.2594,  ..., -0.2448, -0.2740, -0.2740],
           [-0.2448, -0.2594, -0.2448,  ..., -0.2740, -0.2740, -0.2594],
           [-0.2448, -0.2302, -0.2448,  ..., -0.2886, -0.2886, -0.2740],
           ...,
           [ 0.0617,  0.0617,  0.0617,  ...,  0.6603,  0.6603,  0.6457],
           [ 0.0617,  0.0617,  0.0763,  ...,  0.6603,  0.6603,  0.6457],
           [ 0.0763,  0.0763,  0.0763,  ...,  0.6603,  0.6603,  0.6457]],
  
          [[-0.1613, -0.1613, -0.1763,  ..., -0.1613, -0.1913, -0.1913],
           [-0.1763, -0.1763, -0.1613,  ..., -0.1913, -0.1913, -0.1763],
           [-0.1613, -0.1463, -0.1613,  ..., -0.2063, -0.2063, -0.1913],
           ...,
           [ 0.1239,  0.1389,  0.1389,  ...,  0.7092,  0.7092,  0.6942],
           [ 0.1389,  0.1239,  0.1539,  ...,  0.7242,  0.7092,  0.7092],
           [ 0.1389,  0.1389,  0.1539,  ...,  0.7242,  0.7092,  0.7092]],
  
          [[ 0.0129,  0.0271,  0.0129,  ...,  0.0271, -0.0013, -0.0156],
     

In [ ]:
print(train_dataset.class_to_idx)
print(train_dataset.path2label)

['a photo of a blue cone', 'a photo of a blue cube', 'a photo of a blue cylinder', 'a photo of a blue sphere', 'a photo of a brown cone', 'a photo of a brown cube', 'a photo of a brown cylinder', 'a photo of a brown sphere', 'a photo of a cyan cone', 'a photo of a cyan cube', 'a photo of a cyan cylinder', 'a photo of a cyan sphere', 'a photo of a gray cone', 'a photo of a gray cube', 'a photo of a gray cylinder', 'a photo of a gray sphere', 'a photo of a green cone', 'a photo of a green cube', 'a photo of a green cylinder', 'a photo of a green sphere', 'a photo of a purple cone', 'a photo of a purple cube', 'a photo of a purple cylinder', 'a photo of a purple sphere', 'a photo of a red cone', 'a photo of a red cube', 'a photo of a red cylinder', 'a photo of a red sphere', 'a photo of a yellow cone', 'a photo of a yellow cube', 'a photo of a yellow cylinder', 'a photo of a yellow sphere']
{'/content/train30/yellow sphere/CLEVR_new_large_yellow_metal_sphere000088.png': 31, '/content/trai

In [ ]:
i = 0
for k,v in train_dataset.path2label.items():
    i+=1
    print(k,v)
    if i == 10:
        break

/content/train30/yellow sphere/CLEVR_new_large_yellow_metal_sphere000088.png 31
/content/train30/yellow sphere/CLEVR_new_small_yellow_metal_sphere000095.png 31
/content/train30/yellow sphere/CLEVR_new_large_yellow_metal_sphere000024.png 31
/content/train30/yellow sphere/CLEVR_new_large_yellow_rubber_sphere000059.png 31
/content/train30/yellow sphere/CLEVR_new_large_yellow_rubber_sphere000076.png 31
/content/train30/yellow sphere/CLEVR_new_large_yellow_rubber_sphere000033.png 31
/content/train30/yellow sphere/CLEVR_new_small_yellow_metal_sphere000001.png 31
/content/train30/yellow sphere/CLEVR_new_small_yellow_metal_sphere000039.png 31
/content/train30/yellow sphere/CLEVR_new_small_yellow_rubber_sphere000011.png 31
/content/train30/yellow sphere/CLEVR_new_large_yellow_metal_sphere000015.png 31


In [ ]:
# https://github.com/pytorch/pytorch/blob/e5742494f6080c8e6f43c37689fc18a7c4b39dfd/torch/utils/data/dataloader.py#L145
class BalancedBatchSampler(BatchSampler):
    """
    BatchSampler - from a MNIST-like dataset, samples n_classes and within these classes samples n_samples.
    Returns batches of size n_classes * n_samples
    """

    def __init__(self, labels, n_classes, n_samples):
        self.labels = labels
        self.labels_set = list(set(self.labels.numpy()))
        self.label_to_indices = {label: np.where(self.labels.numpy() == label)[0]
                                 for label in self.labels_set}
        for l in self.labels_set:
            np.random.shuffle(self.label_to_indices[l])
        self.used_label_indices_count = {label: 0 for label in self.labels_set}
        self.count = 0
        self.n_classes = n_classes
        self.n_samples = n_samples
        self.n_dataset = len(self.labels)
        self.batch_size = self.n_samples * self.n_classes

    def __iter__(self):
        self.count = 0
        while self.count + self.batch_size < self.n_dataset:
            classes = np.random.choice(self.labels_set, self.n_classes, replace=False)
            indices = []
            for class_ in classes:
                indices.extend(self.label_to_indices[class_][
                               self.used_label_indices_count[class_]:self.used_label_indices_count[
                                                                         class_] + self.n_samples])
                self.used_label_indices_count[class_] += self.n_samples
                if self.used_label_indices_count[class_] + self.n_samples > len(self.label_to_indices[class_]):
                    np.random.shuffle(self.label_to_indices[class_])
                    self.used_label_indices_count[class_] = 0
            yield indices
            self.count += self.n_classes * self.n_samples

    def __len__(self):
        return self.n_dataset // self.batch_size

train_labels = torch.tensor([item[2] for item in train_dataset])
train_sampler = BalancedBatchSampler(train_labels, BATCH_SIZE, 1)
train_dataloader = DataLoader(train_dataset, batch_sampler=train_sampler)

len(train_dataset), train_dataset[0]

(510,
 (tensor([[[-0.2448, -0.2302, -0.2594,  ..., -0.2448, -0.2740, -0.2740],
           [-0.2448, -0.2594, -0.2448,  ..., -0.2740, -0.2740, -0.2594],
           [-0.2448, -0.2302, -0.2448,  ..., -0.2886, -0.2886, -0.2740],
           ...,
           [ 0.0617,  0.0617,  0.0617,  ...,  0.6603,  0.6603,  0.6457],
           [ 0.0617,  0.0617,  0.0763,  ...,  0.6603,  0.6603,  0.6457],
           [ 0.0763,  0.0763,  0.0763,  ...,  0.6603,  0.6603,  0.6457]],
  
          [[-0.1613, -0.1613, -0.1763,  ..., -0.1613, -0.1913, -0.1913],
           [-0.1763, -0.1763, -0.1613,  ..., -0.1913, -0.1913, -0.1763],
           [-0.1613, -0.1463, -0.1613,  ..., -0.2063, -0.2063, -0.1913],
           ...,
           [ 0.1239,  0.1389,  0.1389,  ...,  0.7092,  0.7092,  0.6942],
           [ 0.1389,  0.1239,  0.1539,  ...,  0.7242,  0.7092,  0.7092],
           [ 0.1389,  0.1389,  0.1539,  ...,  0.7242,  0.7092,  0.7092]],
  
          [[ 0.0129,  0.0271,  0.0129,  ...,  0.0271, -0.0013, -0.0156],
     

In [ ]:
for i, item in enumerate(train_sampler):
#     print(item)
#     print(len(item))
    labels = []
    for idx in item:
        label = train_dataset[idx][2]
        labels.append(label)
    break
len(labels), len(set(labels))

(4, 4)

In [ ]:
for batch in train_dataloader:
    imgs, txts, labels = batch
    print(imgs.shape)
    print(len(txts))
    print(labels)
    print(labels.shape)
    print(torch.unique(labels).shape)
    break

torch.Size([4, 3, 224, 224])
4
tensor([27, 22, 11,  5])
torch.Size([4])
torch.Size([4])


In [ ]:
#https://github.com/openai/CLIP/issues/57
def convert_models_to_fp32(model):
    for p in model.parameters():
        p.data = p.data.float()
        p.grad.data = p.grad.data.float()

if device == "cpu":
    model.float()

loss_img = nn.CrossEntropyLoss()
loss_txt = nn.CrossEntropyLoss()
# optimizer = optim.Adam(model.parameters(), lr=5e-5,betas=(0.9,0.98),eps=1e-6,weight_decay=0.2)
optimizer = optim.Adam(model.parameters(), lr=1e-5)
scheduler = optim.lr_scheduler.CosineAnnealingLR(optimizer, len(train_dataloader)*EPOCH)

In [ ]:
best_ep = -1
best_tr_loss = 1e5
#import wandb

torch.use_deterministic_algorithms(False)
# Ensure that CUDA operations are deterministic
#os.environ["CUBLAS_WORKSPACE_CONFIG"] = ":4096:8"


#wandb.init(project='train_clip_relational', name='vit-l14')
for epoch in range(EPOCH):
    print(f"running epoch {epoch}, best train loss {best_tr_loss} after epoch {best_ep}")
    step = 0
    tr_loss = 0
    model.train()
    pbar = tqdm(train_dataloader, leave=False)
    for batch in pbar:
        step += 1
        optimizer.zero_grad()

        images, texts, _ = batch
        images = images.to(device)
        texts = clip.tokenize(texts).to(device)
#         print(images.shape, texts.shape)
        logits_per_image, logits_per_text = model(images, texts)
        ground_truth = torch.arange(BATCH_SIZE).to(device)

        total_loss = (loss_img(logits_per_image,ground_truth) + loss_txt(logits_per_text,ground_truth))/2
        total_loss.backward()
        tr_loss += total_loss.item()
        if device == "cpu":
            optimizer.step()
            scheduler.step()
        else:
            convert_models_to_fp32(model)
            optimizer.step()
            scheduler.step()
            clip.model.convert_weights(model)
        pbar.set_description(f"train batchCE: {total_loss.item()}", refresh=True)
        #wandb.log({'loss': total_loss.item()})
    tr_loss /= step

    if tr_loss < best_tr_loss:
      best_tr_loss = tr_loss
      best_ep = epoch


#wandb.finish()
torch.save(model.state_dict(), "last_model.pt")
print("best_ep", best_ep)

running epoch 0, best train loss 100000.0 after epoch -1


  0%|          | 0/127 [00:00<?, ?it/s]

running epoch 1, best train loss 0.0007198715773154431 after epoch 0


  0%|          | 0/127 [00:00<?, ?it/s]

running epoch 2, best train loss 0.0007198715773154431 after epoch 0


...

running epoch 18, best train loss 0.00024216897844329594 after epoch 10


  0%|          | 0/127 [00:00<?, ?it/s]

running epoch 19, best train loss 0.00024216897844329594 after epoch 10


  0%|          | 0/127 [00:00<?, ?it/s]

best_ep 10


# Two Object

In [ ]:
# get two object data from drive
!cp /content/drive/MyDrive/two_object\ \(1\).zip /content/two_object.zip
!unzip two_object.zip

Streaming output truncated to the last 5000 lines.
  inflating: two_object/train/purple_cone_brown_cube/purple cone/CLEVR_brown_cube_purple_cone_002541.png  
  inflating: two_object/train/purple_cone_brown_cube/purple cone/CLEVR_brown_cube_purple_cone_002536.png  
  inflating: two_object/train/purple_cone_brown_cube/purple cone/CLEVR_brown_cube_purple_cone_002515.png  
  inflating: two_object/train/purple_cone_brown_cube/purple cone/CLEVR_brown_cube_purple_cone_002537.png  
  inflating: two_object/train/purple_cone_brown_cube/purple cone/CLEVR_brown_cube_purple_cone_002504.png  
  inflating: two_object/train/purple_cone_brown_cube/purple cone/CLEVR_brown_cube_purple_cone_002546.png  
  inflating: two_object/train/purple_cone_brown_cube/purple cone/CLEVR_brown_cube_purple_cone_002540.png  
  inflating: two_object/train/purple_cone_brown_cube/purple cone/CLEVR_brown_cube_purple_cone_002528.png  
  inflating: two_object/train/purple_cone_brown_cube/purple cone/CLEVR_brown_cube_purple_cone

In [ ]:
# Get 30 images of each class from train folder

import os
import shutil

source_dir = "/content/two_object/train/"  # Replace with your folder path
destination_dir = "/content/trainTwo30/"  # Replace with your desired test folder path

os.mkdir(destination_dir)

# Loop through each subfolder in the main folder
for subfolder in os.listdir(source_dir):
  # print(subfolder)
  os.mkdir(destination_dir + subfolder)

  for subsubfolder in os.listdir(source_dir + "/" + subfolder):

    print(subsubfolder)

    subfolder_path = os.path.join(source_dir, subfolder)
    subsubfolder_path = os.path.join(subfolder_path, subsubfolder)
    dest_subfolder_path = os.path.join(destination_dir, subfolder)
    dest_subsubfolder_path = os.path.join(dest_subfolder_path, subsubfolder)

    os.mkdir(dest_subsubfolder_path)

    images = [img for img in os.listdir(subsubfolder_path) if img.lower().endswith(('.png', '.jpg', '.jpeg'))]
    print(images)
    for img in images[:30]:
      src_img_path = os.path.join(subsubfolder_path, img)
      dest_img_path = os.path.join(dest_subsubfolder_path, img)

      # Copy each of the 30 images to the corresponding test subfolder
      shutil.move(src_img_path, dest_img_path)


print("Done!")


red sphere
['CLEVR_red_sphere_purple_cylinder_014535.png', 'CLEVR_red_sphere_purple_cylinder_014504.png', 'CLEVR_red_sphere_purple_cylinder_014509.png', 'CLEVR_red_sphere_purple_cylinder_014502.png', 'CLEVR_red_sphere_purple_cylinder_014533.png', 'CLEVR_red_sphere_purple_cylinder_014514.png', 'CLEVR_red_sphere_purple_cylinder_014527.png', 'CLEVR_red_sphere_purple_cylinder_014531.png', 'CLEVR_red_sphere_purple_cylinder_014532.png', 'CLEVR_red_sphere_purple_cylinder_014539.png', 'CLEVR_red_sphere_purple_cylinder_014536.png', 'CLEVR_red_sphere_purple_cylinder_014519.png', 'CLEVR_red_sphere_purple_cylinder_014505.png', 'CLEVR_red_sphere_purple_cylinder_014529.png', 'CLEVR_red_sphere_purple_cylinder_014530.png', 'CLEVR_red_sphere_purple_cylinder_014517.png', 'CLEVR_red_sphere_purple_cylinder_014542.png', 'CLEVR_red_sphere_purple_cylinder_014528.png', 'CLEVR_red_sphere_purple_cylinder_014549.png', 'CLEVR_red_sphere_purple_cylinder_014540.png', 'CLEVR_red_sphere_purple_cylinder_014500.png', '

In [ ]:
!zip -r /content/trainTwo30.zip /content/trainTwo30

Streaming output truncated to the last 5000 lines.
  adding: content/trainTwo30/brown_cone_cyan_cylinder/brown cone/CLEVR_cyan_cylinder_brown_cone_004987.png (deflated 0%)
  adding: content/trainTwo30/brown_cone_cyan_cylinder/brown cone/CLEVR_cyan_cylinder_brown_cone_004985.png (deflated 0%)
  adding: content/trainTwo30/brown_cone_cyan_cylinder/brown cone/CLEVR_cyan_cylinder_brown_cone_004979.png (deflated 0%)
  adding: content/trainTwo30/brown_cone_cyan_cylinder/brown cone/CLEVR_cyan_cylinder_brown_cone_004974.png (deflated 0%)
  adding: content/trainTwo30/brown_cone_cyan_cylinder/brown cone/CLEVR_cyan_cylinder_brown_cone_004999.png (deflated 0%)
  adding: content/trainTwo30/brown_cone_cyan_cylinder/brown cone/CLEVR_cyan_cylinder_brown_cone_004952.png (deflated 0%)
  adding: content/trainTwo30/brown_cone_cyan_cylinder/brown cone/CLEVR_cyan_cylinder_brown_cone_004953.png (deflated 0%)
  adding: content/trainTwo30/brown_cone_cyan_cylinder/brown cone/CLEVR_cyan_cylinder_brown_cone_004967

In [ ]:
d_train = {}
for folder in os.listdir('/content/trainTwo30/'):
  for subfolder in os.listdir('/content/trainTwo30/' + folder):
    for img_path in glob.glob('/content/trainTwo30/' + folder + "/" + subfolder + "/*.png"):
      d_train[img_path] = ["a photo of a " + subfolder]
      print(subfolder)

len(d_train)
print(d_train)

Streaming output truncated to the last 5000 lines.
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
red sphere
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
yellow cone
purple cone
purple cone
purple cone
purple cone
pu

In [ ]:
class ClevrDataset(Dataset):
    def __init__(self, data, preprocess):
        self.preprocess = preprocess
        self.img_paths = []
        self.captions = []
        # Read the CSV files into DataFrames
        classes = pd.read_csv('clevr_beth_train.csv')


        self.class_to_idx = classes['prompt'].tolist()
        for img_path, captions in data.items():
            print(img_path)
            for cap in captions:
                self.img_paths.append(img_path)
                self.captions.append(cap)
        self.processed_cache = {}
        for img_path in data:
            self.processed_cache[img_path] = self.preprocess(Image.open(img_path))
        self.img_paths_set = list(data.keys())

        self.path2label = {path: self.class_to_idx.index("a photo of a " + path.split('/')[4]) for path in self.img_paths_set}

    def __len__(self):
        return len(self.captions)

    def __getitem__(self, idx):
        img_path = self.img_paths[idx]
        image = self.processed_cache[img_path]
        caption = self.captions[idx]
        label = self.path2label[img_path]
        return image, caption, label

train_dataset = ClevrDataset(d_train, preprocess)
len(train_dataset),  train_dataset[0]

/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_purple_cylinder_014535.png
/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_purple_cylinder_014504.png
/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_purple_cylinder_014509.png
/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_purple_cylinder_014502.png
/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_purple_cylinder_014533.png
/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_purple_cylinder_014514.png
/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_purple_cylinder_014527.png
/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_purple_cylinder_014531.png
/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_purple_cylinder_014532.png
/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_purple_

(5580,
 (tensor([[[-0.2302, -0.2448, -0.2448,  ..., -0.2740, -0.2740, -0.2740],
           [-0.2448, -0.2594, -0.2448,  ..., -0.2594, -0.2740, -0.2594],
           [-0.2448, -0.2302, -0.2594,  ..., -0.2740, -0.2740, -0.2740],
           ...,
           [ 0.0763,  0.0909,  0.0763,  ...,  0.5581,  0.5581,  0.5581],
           [ 0.0763,  0.0763,  0.0909,  ...,  0.5727,  0.5581,  0.5581],
           [ 0.0909,  0.0909,  0.1055,  ...,  0.5727,  0.5727,  0.5581]],
  
          [[-0.1463, -0.1613, -0.1613,  ..., -0.1913, -0.1913, -0.1913],
           [-0.1613, -0.1763, -0.1613,  ..., -0.1763, -0.1913, -0.1763],
           [-0.1613, -0.1463, -0.1763,  ..., -0.1913, -0.1913, -0.1913],
           ...,
           [ 0.1539,  0.1689,  0.1539,  ...,  0.6191,  0.6191,  0.6191],
           [ 0.1539,  0.1539,  0.1539,  ...,  0.6191,  0.6191,  0.6191],
           [ 0.1539,  0.1539,  0.1839,  ...,  0.6341,  0.6341,  0.6191]],
  
          [[ 0.0271,  0.0271,  0.0129,  ..., -0.0156, -0.0013, -0.0013],
    

In [ ]:
print(train_dataset.class_to_idx)
print(train_dataset.path2label)

['a photo of a blue cube', 'a photo of a blue sphere', 'a photo of a brown cone', 'a photo of a brown cube', 'a photo of a cyan cylinder', 'a photo of a cyan sphere', 'a photo of a gray cube', 'a photo of a gray sphere', 'a photo of a green cylinder', 'a photo of a green sphere', 'a photo of a purple cone', 'a photo of a purple cylinder', 'a photo of a purple sphere', 'a photo of a red cylinder', 'a photo of a red sphere', 'a photo of a yellow cone', 'a photo of a yellow sphere']
{'/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_purple_cylinder_014535.png': 14, '/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_purple_cylinder_014504.png': 14, '/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_purple_cylinder_014509.png': 14, '/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_purple_cylinder_014502.png': 14, '/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_pu

In [ ]:
i = 0
for k,v in train_dataset.path2label.items():
    i+=1
    print(k,v)
    if i == 10:
        break

/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_purple_cylinder_014535.png 14
/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_purple_cylinder_014504.png 14
/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_purple_cylinder_014509.png 14
/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_purple_cylinder_014502.png 14
/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_purple_cylinder_014533.png 14
/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_purple_cylinder_014514.png 14
/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_purple_cylinder_014527.png 14
/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_purple_cylinder_014531.png 14
/content/trainTwo30/red_sphere_purple_cylinder/red sphere/CLEVR_red_sphere_purple_cylinder_014532.png 14
/content/trainTwo30/red_sphere_purple_cylinder/red sphe

In [ ]:
# https://github.com/pytorch/pytorch/blob/e5742494f6080c8e6f43c37689fc18a7c4b39dfd/torch/utils/data/dataloader.py#L145
class BalancedBatchSampler(BatchSampler):
    """
    BatchSampler - from a MNIST-like dataset, samples n_classes and within these classes samples n_samples.
    Returns batches of size n_classes * n_samples
    """

    def __init__(self, labels, n_classes, n_samples):
        self.labels = labels
        self.labels_set = list(set(self.labels.numpy()))
        self.label_to_indices = {label: np.where(self.labels.numpy() == label)[0]
                                 for label in self.labels_set}
        for l in self.labels_set:
            np.random.shuffle(self.label_to_indices[l])
        self.used_label_indices_count = {label: 0 for label in self.labels_set}
        self.count = 0
        self.n_classes = n_classes
        self.n_samples = n_samples
        self.n_dataset = len(self.labels)
        self.batch_size = self.n_samples * self.n_classes

    def __iter__(self):
        self.count = 0
        while self.count + self.batch_size < self.n_dataset:
            classes = np.random.choice(self.labels_set, self.n_classes, replace=False)
            indices = []
            for class_ in classes:
                indices.extend(self.label_to_indices[class_][
                               self.used_label_indices_count[class_]:self.used_label_indices_count[
                                                                         class_] + self.n_samples])
                self.used_label_indices_count[class_] += self.n_samples
                if self.used_label_indices_count[class_] + self.n_samples > len(self.label_to_indices[class_]):
                    np.random.shuffle(self.label_to_indices[class_])
                    self.used_label_indices_count[class_] = 0
            yield indices
            self.count += self.n_classes * self.n_samples

    def __len__(self):
        return self.n_dataset // self.batch_size

train_labels = torch.tensor([item[2] for item in train_dataset])
train_sampler = BalancedBatchSampler(train_labels, BATCH_SIZE, 1)
train_dataloader = DataLoader(train_dataset, batch_sampler=train_sampler)


In [ ]:
for i, item in enumerate(train_sampler):
#     print(item)
#     print(len(item))
    labels = []
    for idx in item:
        label = train_dataset[idx][2]
        labels.append(label)
    break
len(labels), len(set(labels))

(8, 8)

In [ ]:
for batch in train_dataloader:
    imgs, txts, labels = batch
    print(imgs.shape)
    print(len(txts))
    print(labels)
    print(labels.shape)
    print(torch.unique(labels).shape)
    break

torch.Size([8, 3, 224, 224])
8
tensor([12,  5,  0, 10,  3, 13, 11,  1])
torch.Size([8])
torch.Size([8])


In [ ]:
#https://github.com/openai/CLIP/issues/57
def convert_models_to_fp32(model):
    for p in model.parameters():
        p.data = p.data.float()
        p.grad.data = p.grad.data.float()

if device == "cpu":
    model.float()

loss_img = nn.CrossEntropyLoss()
loss_txt = nn.CrossEntropyLoss()
# optimizer = optim.Adam(model.parameters(), lr=5e-5,betas=(0.9,0.98),eps=1e-6,weight_decay=0.2)
optimizer = optim.Adam(model.parameters(), lr=1e-5)
scheduler = optim.lr_scheduler.CosineAnnealingLR(optimizer, len(train_dataloader)*EPOCH)

In [ ]:
best_te_loss = 1e5
best_ep = -1
best_tr_loss = 1e5
#import wandb

torch.use_deterministic_algorithms(False)
# Ensure that CUDA operations are deterministic
#os.environ["CUBLAS_WORKSPACE_CONFIG"] = ":4096:8"


#wandb.init(project='train_clip_relational', name='vit-l14')
for epoch in range(EPOCH):
    print(f"running epoch {epoch}, best train loss {best_tr_loss} after epoch {best_ep}")
    step = 0
    tr_loss = 0
    model.train()
    pbar = tqdm(train_dataloader, leave=False)
    for batch in pbar:
        step += 1
        optimizer.zero_grad()

        images, texts, _ = batch
        images = images.to(device)
        texts = clip.tokenize(texts).to(device)
#         print(images.shape, texts.shape)
        logits_per_image, logits_per_text = model(images, texts)
        ground_truth = torch.arange(BATCH_SIZE).to(device)

        total_loss = (loss_img(logits_per_image,ground_truth) + loss_txt(logits_per_text,ground_truth))/2
        total_loss.backward()
        tr_loss += total_loss.item()
        if device == "cpu":
            optimizer.step()
            scheduler.step()
        else:
            convert_models_to_fp32(model)
            optimizer.step()
            scheduler.step()
            clip.model.convert_weights(model)
        pbar.set_description(f"train batchCE: {total_loss.item()}", refresh=True)
        #wandb.log({'loss': total_loss.item()})
    tr_loss /= step

    if tr_loss < best_tr_loss:
      best_tr_loss = tr_loss
      best_ep = epoch


#wandb.finish()
torch.save(model.state_dict(), "last_model.pt")
print("best_ep", best_ep)

running epoch 0, best train loss 100000.0 after epoch -1


  0%|          | 0/697 [00:00<?, ?it/s]

running epoch 1, best train loss 0.32241049045469705 after epoch 0


  0%|          | 0/697 [00:00<?, ?it/s]

running epoch 2, best train loss 0.3208868937991784 after epoch 1


...

running epoch 18, best train loss 0.2819426754112736 after epoch 17


  0%|          | 0/697 [00:00<?, ?it/s]

running epoch 19, best train loss 0.2819426754112736 after epoch 17


  0%|          | 0/697 [00:00<?, ?it/s]

best_ep 17


# Relational

In [ ]:
!cp /content/drive/MyDrive/relational.zip /content/
!unzip relational.zip

Archive:  relational.zip
   creating: relational/
   creating: relational/val/
   creating: relational/val/cube left cone/
  inflating: relational/val/cube left cone/CLEVR_rel_000019.png  
  inflating: relational/val/cube left cone/CLEVR_rel_000305.png  
  inflating: relational/val/cube left cone/CLEVR_rel_000324.png  
  inflating: relational/val/cube left cone/CLEVR_rel_000775.png  
  inflating: relational/val/cube left cone/CLEVR_rel_000253.png  
  inflating: relational/val/cube left cone/CLEVR_rel_000339.png  
  inflating: relational/val/cube left cone/CLEVR_rel_000164.png  
  inflating: relational/val/cube left cone/CLEVR_rel_000619.png  
  inflating: relational/val/cube left cone/CLEVR_rel_000149.png  
  inflating: relational/val/cube left cone/CLEVR_rel_000492.png  
  inflating: relational/val/cube left cone/CLEVR_rel_000038.png  
  inflating: relational/val/cube left cone/CLEVR_rel_000203.png  
  inflating: relational/val/cube left cone/CLEVR_rel_000097.png  
  inflating: relati

In [ ]:
# prompt: randomly sample 30 images from each subfolder in single_object/train and put in a new folder with the same subfolders as single_object/train

import shutil
import os

def sample_images(source_dir, dest_dir, num_samples):
  if not os.path.exists(dest_dir):
    os.makedirs(dest_dir)

  # make subfolders in destination folder
  for subfolder in os.listdir(source_dir):
    if not os.path.exists(os.path.join(dest_dir, subfolder)):
      os.makedirs(os.path.join(dest_dir, subfolder))

    subfolder_path = os.path.join(source_dir, subfolder)

    # take random images so there's still a mix of sizes/materials in the new folder
    images = [f for f in os.listdir(subfolder_path)]
    random_images = random.sample(images, min(num_samples, len(images)))
    for image in random_images:
      shutil.copy(os.path.join(subfolder_path, image), os.path.join(dest_dir, subfolder, image))



# Example usage:
source_dir = 'relational/train'
dest_dir = 'rel40'
sample_images(source_dir, dest_dir, 40)


In [ ]:
!rm -r relational

In [ ]:
!zip -r rel40.zip rel40/

updating: rel40/ (stored 0%)
  adding: rel40/sphere right cube/ (stored 0%)
  adding: rel40/sphere right cube/CLEVR_rel_000137.png (deflated 0%)
  adding: rel40/sphere right cube/CLEVR_rel_000160.png (deflated 0%)
  adding: rel40/sphere right cube/CLEVR_rel_000557.png (deflated 0%)
  adding: rel40/sphere right cube/CLEVR_rel_000325.png (deflated 0%)
  adding: rel40/sphere right cube/CLEVR_rel_000271.png (deflated 0%)
  adding: rel40/sphere right cube/CLEVR_rel_000670.png (deflated 0%)
  adding: rel40/sphere right cube/CLEVR_rel_000724.png (deflated 0%)
  adding: rel40/sphere right cube/CLEVR_rel_000509.png (deflated 0%)
  adding: rel40/sphere right cube/CLEVR_rel_000189.png (deflated 0%)
  adding: rel40/sphere right cube/CLEVR_rel_000191.png (deflated 0%)
  adding: rel40/sphere right cube/CLEVR_rel_000621.png (deflated 0%)
  adding: rel40/sphere right cube/CLEVR_rel_000228.png (deflated 0%)
  adding: rel40/sphere right cube/CLEVR_rel_000129.png (deflated 0%)
  adding: rel40/sphere righ

In [ ]:
d_train = {}
for folder in os.listdir('/content/rel40/'):
  for img_path in glob.glob('/content/rel40/' + folder + "/*.png"):
    d_train[img_path] = ["a photo of a " + folder]

len(d_train)

440

In [ ]:
class ClevrDataset(Dataset):
    def __init__(self, data, preprocess):
        self.preprocess = preprocess
        self.img_paths = []
        self.captions = []
        # Read the CSV files into DataFrames
        classes = pd.read_csv('relational_train_prompts.csv')



        self.class_to_idx = classes['prompt'].tolist()
        for img_path, captions in data.items():
            for cap in captions:
                self.img_paths.append(img_path)
                self.captions.append(cap)
        self.processed_cache = {}
        for img_path in data:
            self.processed_cache[img_path] = self.preprocess(Image.open(img_path))
        self.img_paths_set = list(data.keys())
        print(self.img_paths_set)
        for p in self.img_paths_set:
          print(p.split('/'))
        self.path2label = {path: self.class_to_idx.index("a photo of a " + path.split('/')[3]) for path in self.img_paths_set}

    def __len__(self):
        return len(self.captions)

    def __getitem__(self, idx):
        img_path = self.img_paths[idx]
        image = self.processed_cache[img_path]
        caption = self.captions[idx]
        label = self.path2label[img_path]
        return image, caption, label

train_dataset = ClevrDataset(d_train, preprocess)
len(train_dataset), train_dataset[0]

['/content/rel40/sphere right cube/CLEVR_rel_000137.png', '/content/rel40/sphere right cube/CLEVR_rel_000160.png', '/content/rel40/sphere right cube/CLEVR_rel_000557.png', '/content/rel40/sphere right cube/CLEVR_rel_000325.png', '/content/rel40/sphere right cube/CLEVR_rel_000271.png', '/content/rel40/sphere right cube/CLEVR_rel_000670.png', '/content/rel40/sphere right cube/CLEVR_rel_000724.png', '/content/rel40/sphere right cube/CLEVR_rel_000509.png', '/content/rel40/sphere right cube/CLEVR_rel_000189.png', '/content/rel40/sphere right cube/CLEVR_rel_000191.png', '/content/rel40/sphere right cube/CLEVR_rel_000621.png', '/content/rel40/sphere right cube/CLEVR_rel_000228.png', '/content/rel40/sphere right cube/CLEVR_rel_000129.png', '/content/rel40/sphere right cube/CLEVR_rel_000369.png', '/content/rel40/sphere right cube/CLEVR_rel_000318.png', '/content/rel40/sphere right cube/CLEVR_rel_000443.png', '/content/rel40/sphere right cube/CLEVR_rel_000092.png', '/content/rel40/sphere right c

(440,
 (tensor([[[-0.2594, -0.2594, -0.2448,  ..., -0.2886, -0.2740, -0.2594],
           [-0.2594, -0.2740, -0.2448,  ..., -0.2594, -0.2740, -0.2740],
           [-0.2594, -0.2448, -0.2740,  ..., -0.2740, -0.2594, -0.2740],
           ...,
           [ 0.0617,  0.0763,  0.0763,  ...,  0.5581,  0.5581,  0.5581],
           [ 0.0617,  0.0763,  0.0763,  ...,  0.5581,  0.5581,  0.5581],
           [ 0.0763,  0.0763,  0.0909,  ...,  0.5727,  0.5727,  0.5581]],
  
          [[-0.1763, -0.1763, -0.1613,  ..., -0.2063, -0.2063, -0.1763],
           [-0.1763, -0.1913, -0.1613,  ..., -0.1763, -0.1913, -0.1913],
           [-0.1763, -0.1613, -0.1913,  ..., -0.1913, -0.1763, -0.1913],
           ...,
           [ 0.1389,  0.1539,  0.1389,  ...,  0.6191,  0.6191,  0.6191],
           [ 0.1389,  0.1539,  0.1539,  ...,  0.6191,  0.6191,  0.6191],
           [ 0.1539,  0.1539,  0.1689,  ...,  0.6341,  0.6341,  0.6191]],
  
          [[-0.0013,  0.0129,  0.0129,  ..., -0.0156, -0.0156, -0.0013],
     

In [ ]:
print(train_dataset.class_to_idx)
print(train_dataset.path2label)

['a photo of a cone right cylinder', 'a photo of a cone right sphere', 'a photo of a cube left sphere', 'a photo of a cube right cylinder', 'a photo of a cube right sphere', 'a photo of a cylinder left cone', 'a photo of a cylinder left cube', 'a photo of a cylinder left sphere', 'a photo of a sphere left cone', 'a photo of a sphere left cube', 'a photo of a sphere right cube']
{'/content/rel40/sphere right cube/CLEVR_rel_000137.png': 10, '/content/rel40/sphere right cube/CLEVR_rel_000160.png': 10, '/content/rel40/sphere right cube/CLEVR_rel_000557.png': 10, '/content/rel40/sphere right cube/CLEVR_rel_000325.png': 10, '/content/rel40/sphere right cube/CLEVR_rel_000271.png': 10, '/content/rel40/sphere right cube/CLEVR_rel_000670.png': 10, '/content/rel40/sphere right cube/CLEVR_rel_000724.png': 10, '/content/rel40/sphere right cube/CLEVR_rel_000509.png': 10, '/content/rel40/sphere right cube/CLEVR_rel_000189.png': 10, '/content/rel40/sphere right cube/CLEVR_rel_000191.png': 10, '/conten

In [ ]:
i = 0
for k,v in train_dataset.path2label.items():
    i+=1
    print(k,v)
    if i == 10:
        break

/content/rel40/sphere right cube/CLEVR_rel_000137.png 10
/content/rel40/sphere right cube/CLEVR_rel_000160.png 10
/content/rel40/sphere right cube/CLEVR_rel_000557.png 10
/content/rel40/sphere right cube/CLEVR_rel_000325.png 10
/content/rel40/sphere right cube/CLEVR_rel_000271.png 10
/content/rel40/sphere right cube/CLEVR_rel_000670.png 10
/content/rel40/sphere right cube/CLEVR_rel_000724.png 10
/content/rel40/sphere right cube/CLEVR_rel_000509.png 10
/content/rel40/sphere right cube/CLEVR_rel_000189.png 10
/content/rel40/sphere right cube/CLEVR_rel_000191.png 10


In [ ]:
# https://github.com/pytorch/pytorch/blob/e5742494f6080c8e6f43c37689fc18a7c4b39dfd/torch/utils/data/dataloader.py#L145
class BalancedBatchSampler(BatchSampler):
    """
    BatchSampler - from a MNIST-like dataset, samples n_classes and within these classes samples n_samples.
    Returns batches of size n_classes * n_samples
    """

    def __init__(self, labels, n_classes, n_samples):
        self.labels = labels
        self.labels_set = list(set(self.labels.numpy()))
        self.label_to_indices = {label: np.where(self.labels.numpy() == label)[0]
                                 for label in self.labels_set}
        for l in self.labels_set:
            np.random.shuffle(self.label_to_indices[l])
        self.used_label_indices_count = {label: 0 for label in self.labels_set}
        self.count = 0
        self.n_classes = n_classes
        self.n_samples = n_samples
        self.n_dataset = len(self.labels)
        self.batch_size = self.n_samples * self.n_classes

    def __iter__(self):
        self.count = 0
        while self.count + self.batch_size < self.n_dataset:
            classes = np.random.choice(self.labels_set, self.n_classes, replace=False)
            indices = []
            for class_ in classes:
                indices.extend(self.label_to_indices[class_][
                               self.used_label_indices_count[class_]:self.used_label_indices_count[
                                                                         class_] + self.n_samples])
                self.used_label_indices_count[class_] += self.n_samples
                if self.used_label_indices_count[class_] + self.n_samples > len(self.label_to_indices[class_]):
                    np.random.shuffle(self.label_to_indices[class_])
                    self.used_label_indices_count[class_] = 0
            yield indices
            self.count += self.n_classes * self.n_samples

    def __len__(self):
        return self.n_dataset // self.batch_size

train_labels = torch.tensor([item[2] for item in train_dataset])
train_sampler = BalancedBatchSampler(train_labels, BATCH_SIZE, 1)
train_dataloader = DataLoader(train_dataset, batch_sampler=train_sampler)


In [ ]:
for i, item in enumerate(train_sampler):
#     print(item)
#     print(len(item))
    labels = []
    for idx in item:
        label = train_dataset[idx][2]
        labels.append(label)
    break
len(labels), len(set(labels))

(8, 8)

In [ ]:
for batch in train_dataloader:
    imgs, txts, labels = batch
    print(imgs.shape)
    print(len(txts))
    print(labels)
    print(labels.shape)
    print(torch.unique(labels).shape)
    break

torch.Size([8, 3, 224, 224])
8
tensor([ 5,  6,  2,  9,  0,  1,  3, 10])
torch.Size([8])
torch.Size([8])


In [ ]:
#https://github.com/openai/CLIP/issues/57
def convert_models_to_fp32(model):
    for p in model.parameters():
        p.data = p.data.float()
        p.grad.data = p.grad.data.float()

if device == "cpu":
    model.float()

loss_img = nn.CrossEntropyLoss()
loss_txt = nn.CrossEntropyLoss()
# optimizer = optim.Adam(model.parameters(), lr=5e-5,betas=(0.9,0.98),eps=1e-6,weight_decay=0.2)
optimizer = optim.Adam(model.parameters(), lr=1e-5)
scheduler = optim.lr_scheduler.CosineAnnealingLR(optimizer, len(train_dataloader)*EPOCH)

In [ ]:
best_ep = -1
best_tr_loss = 1e5
#import wandb

torch.use_deterministic_algorithms(False)
# Ensure that CUDA operations are deterministic
#os.environ["CUBLAS_WORKSPACE_CONFIG"] = ":4096:8"


#wandb.init(project='train_clip_relational', name='vit-l14')
for epoch in range(EPOCH):
    print(f"running epoch {epoch}, best train loss {best_tr_loss} after epoch {best_ep}")
    step = 0
    tr_loss = 0
    model.train()
    pbar = tqdm(train_dataloader, leave=False)
    for batch in pbar:
        step += 1
        optimizer.zero_grad()

        images, texts, _ = batch
        images = images.to(device)
        texts = clip.tokenize(texts).to(device)
#         print(images.shape, texts.shape)
        logits_per_image, logits_per_text = model(images, texts)
        ground_truth = torch.arange(BATCH_SIZE).to(device)

        total_loss = (loss_img(logits_per_image,ground_truth) + loss_txt(logits_per_text,ground_truth))/2
        total_loss.backward()
        tr_loss += total_loss.item()
        if device == "cpu":
            optimizer.step()
            scheduler.step()
        else:
            convert_models_to_fp32(model)
            optimizer.step()
            scheduler.step()
            clip.model.convert_weights(model)
        pbar.set_description(f"train batchCE: {total_loss.item()}", refresh=True)
        #wandb.log({'loss': total_loss.item()})
    tr_loss /= step

    if tr_loss < best_tr_loss:
      best_tr_loss = tr_loss
      best_ep = epoch


#wandb.finish()
torch.save(model.state_dict(), "last_model.pt")
print("best_ep", best_ep)

running epoch 0, best train loss 100000.0 after epoch -1


  0%|          | 0/55 [00:00<?, ?it/s]

running epoch 1, best train loss 0.49803105107060186 after epoch 0


  0%|          | 0/55 [00:00<?, ?it/s]

running epoch 2, best train loss 0.4499466507523148 after epoch 1


...

running epoch 18, best train loss 0.31434235749421297 after epoch 12


  0%|          | 0/55 [00:00<?, ?it/s]

running epoch 19, best train loss 0.3140224880642361 after epoch 18


  0%|          | 0/55 [00:00<?, ?it/s]

best_ep 19
